In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import optuna
from xgboost import XGBRegressor
from catboost import CatBoostRegressor
from lightgbm import LGBMRegressor
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_log_error

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/playground-series-s4e4/sample_submission.csv
/kaggle/input/playground-series-s4e4/train.csv
/kaggle/input/playground-series-s4e4/test.csv


In [2]:
def rmsle_score(y_true, y_pred):
    
    msle = mean_squared_log_error(y_true, y_pred)
    rmsle = np.sqrt(msle)
    return rmsle

In [3]:
test = pd.read_csv('/kaggle/input/playground-series-s4e4/test.csv')
train = pd.read_csv('/kaggle/input/playground-series-s4e4/train.csv')

In [4]:
train = pd.get_dummies(train, columns=['Sex'])
test = pd.get_dummies(test, columns=['Sex'])

In [5]:
X_train = train.drop(['Rings', 'id'], axis=1)
y_train = train['Rings']

X_test = test.drop('id', axis=1)

In [6]:
X_train_t, X_val_t, y_train_t, y_val_t = train_test_split(X_train, y_train, test_size=0.33, random_state=42)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.33, random_state=42)

In [7]:
 def objective(trial):
    # Define hyperparameters to be optimized
    params = {
        'iterations': 1000,
        'learning_rate': trial.suggest_float('learning_rate', 0.0001, 0.1),
        'depth': trial.suggest_int('depth', 4, 16),
        'subsample': trial.suggest_float('subsample', 0.1, 1.0),
        'colsample_bylevel': trial.suggest_float('colsample_bylevel', 0.1, 1.0),
        'random_strength': trial.suggest_float('random_strength', 1e-3, 100),
        'min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 1, 100),
        'bagging_temperature': trial.suggest_float('bagging_temperature', 0.0, 10.0),
        'od_type': 'Iter',
        'od_wait': 20,
        'loss_function': 'RMSE',
        'random_state': 42,
        'verbose': False
    }
    
    # Train CatBoostRegressor
    model = CatBoostRegressor(**params)
    model.fit(X_train_t, y_train_t, early_stopping_rounds=20, verbose=False)
    
    # Make predictions
    y_pred = model.predict(X_val_t)
    
    # Calculate RMSE
    score = rmsle_score(y_val_t, y_pred)
    
    return score

study = optuna.create_study(direction='minimize')

study.optimize(objective, n_trials=100)

best_params = study.best_params

print('Best parameters:', best_params)
print('Best RMSE:', study.best_value)

[I 2024-04-23 20:59:26,615] A new study created in memory with name: no-name-19d6acf4-4da7-4f6c-9822-02c516c74f82
[I 2024-04-23 20:59:35,097] Trial 0 finished with value: 0.15144324934793424 and parameters: {'learning_rate': 0.09233829151692492, 'depth': 7, 'subsample': 0.9470889320890887, 'colsample_bylevel': 0.8989586685060578, 'random_strength': 31.551943163589325, 'min_data_in_leaf': 94, 'bagging_temperature': 7.2146494179512235}. Best is trial 0 with value: 0.15144324934793424.
[I 2024-04-23 20:59:59,420] Trial 1 finished with value: 0.15226085590059088 and parameters: {'learning_rate': 0.03195827281631759, 'depth': 11, 'subsample': 0.4353453574107694, 'colsample_bylevel': 0.8490781340018747, 'random_strength': 95.84354108693896, 'min_data_in_leaf': 39, 'bagging_temperature': 4.84521978329351}. Best is trial 0 with value: 0.15144324934793424.
[I 2024-04-23 21:00:49,177] Trial 2 finished with value: 0.1542576220652791 and parameters: {'learning_rate': 0.0906450983346801, 'depth': 1

Best parameters: {'learning_rate': 0.07847519483647242, 'depth': 7, 'subsample': 0.9975473252053483, 'colsample_bylevel': 0.8969706149173187, 'random_strength': 35.463590658889075, 'min_data_in_leaf': 85, 'bagging_temperature': 9.326143894586169}
Best RMSE: 0.15126164385321236


In [8]:
model = CatBoostRegressor(**best_params)
model.fit(X_train, y_train)

y_pred_val = model.predict(X_val)
rmsle_val = rmsle_score(y_pred_val, y_val)

print('RMSLE of validation is: ', rmsle_val)

0:	learn: 3.0773450	total: 8.32ms	remaining: 8.31s
1:	learn: 2.9886408	total: 16.6ms	remaining: 8.28s
2:	learn: 2.8968135	total: 25.5ms	remaining: 8.46s
3:	learn: 2.8144603	total: 34.5ms	remaining: 8.58s
4:	learn: 2.7397268	total: 41.8ms	remaining: 8.32s
5:	learn: 2.6802505	total: 49.8ms	remaining: 8.25s
6:	learn: 2.6304047	total: 58.5ms	remaining: 8.3s
7:	learn: 2.5749880	total: 67ms	remaining: 8.3s
8:	learn: 2.5349356	total: 75ms	remaining: 8.26s
9:	learn: 2.4949257	total: 83.7ms	remaining: 8.28s
10:	learn: 2.4644846	total: 91.2ms	remaining: 8.2s
11:	learn: 2.4377772	total: 99.7ms	remaining: 8.2s
12:	learn: 2.4129455	total: 108ms	remaining: 8.18s
13:	learn: 2.3849918	total: 115ms	remaining: 8.1s
14:	learn: 2.3589208	total: 124ms	remaining: 8.12s
15:	learn: 2.3425123	total: 132ms	remaining: 8.11s
16:	learn: 2.3204341	total: 140ms	remaining: 8.07s
17:	learn: 2.3020436	total: 147ms	remaining: 8.04s
18:	learn: 2.2916761	total: 155ms	remaining: 7.99s
19:	learn: 2.2776304	total: 165ms	rema

In [9]:
 def objective(trial):
    # Define hyperparameters to be optimized
    params = {
        'n_estimators': 1000,
        'max_depth': trial.suggest_int('max_depth', 1, 10),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1, log=True),
        'subsample': trial.suggest_float('subsample', 0.1, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.05, 1.0),
        'gamma': trial.suggest_float('gamma', 1e-2, 1.0),
        'min_child_weight': trial.suggest_int('min_child_weight',1, 100),
        'eval_metric': 'rmse',
        'objective': 'reg:squarederror'
    }
    
    # Train XGBRegressor
    model = XGBRegressor(**params)
    model.fit(X_train_t, y_train_t, verbose=False)
    
    # Make predictions
    y_pred = model.predict(X_val_t)
    
    # Calculate RMSE
    score = rmsle_score(y_val_t, y_pred)
    
    return score

study = optuna.create_study(direction='minimize')

study.optimize(objective, n_trials=100)

best_params_xgb = study.best_params

print('Best parameters:', best_params_xgb)
print('Best RMSE:', study.best_value)

[I 2024-04-23 21:50:06,452] A new study created in memory with name: no-name-5def98b6-bf68-4ea1-b0a8-bf71eb453fb7
[I 2024-04-23 21:50:08,869] Trial 0 finished with value: 0.15169751224417027 and parameters: {'max_depth': 4, 'learning_rate': 0.09304373351679926, 'subsample': 0.5068323051514501, 'colsample_bytree': 0.9221206027703182, 'gamma': 0.8737967923005153, 'min_child_weight': 45}. Best is trial 0 with value: 0.15169751224417027.
[I 2024-04-23 21:50:11,522] Trial 1 finished with value: 0.15183134792950648 and parameters: {'max_depth': 4, 'learning_rate': 0.04375146573926776, 'subsample': 0.5685435517647348, 'colsample_bytree': 0.5311058764060478, 'gamma': 0.27871787946192544, 'min_child_weight': 79}. Best is trial 0 with value: 0.15169751224417027.
[I 2024-04-23 21:50:13,850] Trial 2 finished with value: 0.16710694538445642 and parameters: {'max_depth': 4, 'learning_rate': 0.04924153594781839, 'subsample': 0.24614438404846442, 'colsample_bytree': 0.07498977159552801, 'gamma': 0.541

Best parameters: {'max_depth': 8, 'learning_rate': 0.021499523404830356, 'subsample': 0.7051204095377521, 'colsample_bytree': 0.8779529097783333, 'gamma': 0.9187577710077584, 'min_child_weight': 36}
Best RMSE: 0.1509472596080602


In [10]:
model = XGBRegressor(**best_params_xgb)
model.fit(X_train, y_train)

y_pred_val = model.predict(X_val)
rmsle_val = rmsle_score(y_pred_val, y_val)

print('RMSLE of validation is: ', rmsle_val)

RMSLE of validation is:  0.15609152680566488


In [15]:
 def objective(trial):
    # Define hyperparameters to be optimized
    params = {
        'n_estimators': 1000,
        'max_depth': trial.suggest_int('max_depth', 1,10),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 1, 100),
        'min_child_samples': trial.suggest_int('min_child_samples', 10, 60),
        'num_leaves': trial.suggest_int('num_leaves', 8, 128),
        'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.1),
        'subsample': trial.suggest_float('subsample', 0.1,1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.3, 1.0),
        'lambda_l1': trial.suggest_float('lambda_l1', 1e-8, 10.0, log=True),
        'lambda_l2': trial.suggest_float('lambda_l2', 1e-8, 10.0, log=True),
        'reg_alpha': trial.suggest_float('reg_alpha', 0.5, 1.0),
        'reg_lambda': trial.suggest_float('reg_lambda', 0.5, 1.0),
        "metric":'rmse',
        "bagging_freq": 1,
        "boosting_type": "gbdt",    
        "objective":'regression'
    }
    
    # Train LGBMRegressor
    model = LGBMRegressor(**params)
    model.fit(X_train_t, y_train_t)
    
    # Make predictions
    y_pred = model.predict(X_val_t)
    
    # Calculate RMSE
    score = rmsle_score(y_val_t, y_pred)
    
    return score

study = optuna.create_study(direction='minimize')

study.optimize(objective, n_trials=100)

best_params_lgbm = study.best_params

print('Best parameters:', best_params)
print('Best RMSE:', study.best_value)

[I 2024-04-23 22:16:04,055] A new study created in memory with name: no-name-b87956bf-fb29-4ec3-92da-e79cdb15f5e3


[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=39 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] lambda_l2 is set=1.2071374781225607e-05, reg_lambda=0.9573319923091769 will be ignored. Current value: lambda_l2=1.2071374781225607e-05
[LightGBM] [Warning] lambda_l1 is set=4.932294828165869e-06, reg_alpha=0.8298144242571328 will be ignored. Current value: lambda_l1=4.932294828165869e-06
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=100, min_child_samples=39 will be ignored. Current value: min_data_in_leaf=100
[LightGBM] [Warning] lambda_l2 is set=1.2071374781225607e-05, reg_lambda=0.9573319923091769 will be ignored. Current value: lambda_l2=1.2071374781225607e-05
[LightGBM] [Warning] lambda_l1 is set=4.932294828165869e-06, reg_alpha=0.8298144242571328 will b

[I 2024-04-23 22:16:14,626] Trial 0 finished with value: 0.15099425892296298 and parameters: {'max_depth': 8, 'min_data_in_leaf': 100, 'min_child_samples': 39, 'num_leaves': 86, 'learning_rate': 0.043288980697533536, 'subsample': 0.46688964061852867, 'colsample_bytree': 0.6968257986945096, 'lambda_l1': 4.932294828165869e-06, 'lambda_l2': 1.2071374781225607e-05, 'reg_alpha': 0.8298144242571328, 'reg_lambda': 0.9573319923091769}. Best is trial 0 with value: 0.15099425892296298.


[LightGBM] [Warning] min_data_in_leaf is set=18, min_child_samples=50 will be ignored. Current value: min_data_in_leaf=18
[LightGBM] [Warning] lambda_l2 is set=3.2047806969916572, reg_lambda=0.6618399797044449 will be ignored. Current value: lambda_l2=3.2047806969916572
[LightGBM] [Warning] lambda_l1 is set=0.45910569401059004, reg_alpha=0.8609185639953244 will be ignored. Current value: lambda_l1=0.45910569401059004
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=18, min_child_samples=50 will be ignored. Current value: min_data_in_leaf=18
[LightGBM] [Warning] lambda_l2 is set=3.2047806969916572, reg_lambda=0.6618399797044449 will be ignored. Current value: lambda_l2=3.2047806969916572
[LightGBM] [Warning] lambda_l1 is set=0.45910569401059004, reg_alpha=0.8609185639953244 will be ignored. Current value: 

[I 2024-04-23 22:16:23,093] Trial 1 finished with value: 0.15112364814963328 and parameters: {'max_depth': 6, 'min_data_in_leaf': 18, 'min_child_samples': 50, 'num_leaves': 47, 'learning_rate': 0.060061775109485654, 'subsample': 0.6456746660830376, 'colsample_bytree': 0.5638591632769048, 'lambda_l1': 0.45910569401059004, 'lambda_l2': 3.2047806969916572, 'reg_alpha': 0.8609185639953244, 'reg_lambda': 0.6618399797044449}. Best is trial 0 with value: 0.15099425892296298.


...

[LightGBM] [Warning] min_data_in_leaf is set=32, min_child_samples=35 will be ignored. Current value: min_data_in_leaf=32
[LightGBM] [Warning] lambda_l2 is set=0.00015995797710098762, reg_lambda=0.8538942521594856 will be ignored. Current value: lambda_l2=0.00015995797710098762
[LightGBM] [Warning] lambda_l1 is set=0.00035572019131582865, reg_alpha=0.9743055385226789 will be ignored. Current value: lambda_l1=0.00035572019131582865
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=32, min_child_samples=35 will be ignored. Current value: min_data_in_leaf=32
[LightGBM] [Warning] lambda_l2 is set=0.00015995797710098762, reg_lambda=0.8538942521594856 will be ignored. Current value: lambda_l2=0.00015995797710098762
[LightGBM] [Warning] lambda_l1 is set=0.00035572019131582865, reg_alpha=0.9743055385226789 will be

[I 2024-04-23 22:36:20,588] Trial 98 finished with value: 0.15054241509506264 and parameters: {'max_depth': 10, 'min_data_in_leaf': 32, 'min_child_samples': 35, 'num_leaves': 128, 'learning_rate': 0.01004874429782635, 'subsample': 0.8078650839491227, 'colsample_bytree': 0.6833719728852891, 'lambda_l1': 0.00035572019131582865, 'lambda_l2': 0.00015995797710098762, 'reg_alpha': 0.9743055385226789, 'reg_lambda': 0.8538942521594856}. Best is trial 96 with value: 0.1504466225735169.


[LightGBM] [Warning] min_data_in_leaf is set=29, min_child_samples=38 will be ignored. Current value: min_data_in_leaf=29
[LightGBM] [Warning] lambda_l2 is set=5.824449230745465e-05, reg_lambda=0.846048909125479 will be ignored. Current value: lambda_l2=5.824449230745465e-05
[LightGBM] [Warning] lambda_l1 is set=0.0002471267244197553, reg_alpha=0.9283024302101325 will be ignored. Current value: lambda_l1=0.0002471267244197553
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=29, min_child_samples=38 will be ignored. Current value: min_data_in_leaf=29
[LightGBM] [Warning] lambda_l2 is set=5.824449230745465e-05, reg_lambda=0.846048909125479 will be ignored. Current value: lambda_l2=5.824449230745465e-05
[LightGBM] [Warning] lambda_l1 is set=0.0002471267244197553, reg_alpha=0.9283024302101325 will be ignored.

[I 2024-04-23 22:36:34,627] Trial 99 finished with value: 0.15044634159622816 and parameters: {'max_depth': 10, 'min_data_in_leaf': 29, 'min_child_samples': 38, 'num_leaves': 128, 'learning_rate': 0.01595481801894882, 'subsample': 0.8459130714329174, 'colsample_bytree': 0.6028335071998467, 'lambda_l1': 0.0002471267244197553, 'lambda_l2': 5.824449230745465e-05, 'reg_alpha': 0.9283024302101325, 'reg_lambda': 0.846048909125479}. Best is trial 99 with value: 0.15044634159622816.


Best parameters: {'learning_rate': 0.07847519483647242, 'depth': 7, 'subsample': 0.9975473252053483, 'colsample_bylevel': 0.8969706149173187, 'random_strength': 35.463590658889075, 'min_data_in_leaf': 85, 'bagging_temperature': 9.326143894586169}
Best RMSE: 0.15044634159622816


In [16]:
model = LGBMRegressor(**best_params_lgbm)
model.fit(X_train, y_train)

y_pred_val = model.predict(X_val)
rmsle_val = rmsle_score(y_pred_val, y_val)

print('RMSLE of validation is: ', rmsle_val)

[LightGBM] [Warning] min_data_in_leaf is set=29, min_child_samples=38 will be ignored. Current value: min_data_in_leaf=29
[LightGBM] [Warning] lambda_l2 is set=5.824449230745465e-05, reg_lambda=0.846048909125479 will be ignored. Current value: lambda_l2=5.824449230745465e-05
[LightGBM] [Warning] lambda_l1 is set=0.0002471267244197553, reg_alpha=0.9283024302101325 will be ignored. Current value: lambda_l1=0.0002471267244197553
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] min_data_in_leaf is set=29, min_child_samples=38 will be ignored. Current value: min_data_in_leaf=29
[LightGBM] [Warning] lambda_l2 is set=5.824449230745465e-05, reg_lambda=0.846048909125479 will be ignored. Current value: lambda_l2=5.824449230745465e-05
[LightGBM] [Warning] lambda_l1 is set=0.0002471267244197553, reg_alpha=0.9283024302101325 will be ignored. Current value: lambda_l1=0.0002471267244197553
[LightGBM] [Info] Auto-choosing col-wise multi-threading, th